In [2]:
from numpy import zeros
from numpy import ones
from numpy.random import randint
from keras.optimizers import Adam
from keras.initializers import RandomNormal
from keras.models import Model
from keras import Input
from keras.layers import Conv2D
from keras.layers import Conv2DTranspose
from keras.layers import LeakyReLU
from keras.layers import Activation
from keras.layers import Concatenate
from keras.layers import Dropout
from keras.layers import BatchNormalization
from matplotlib import pyplot as plt
from tensorflow.keras.utils import plot_model
import os

In [3]:
def define_discriminator(image_shape):
    
	init = RandomNormal(stddev=0.02)
    
	in_src_image = Input(shape=image_shape)
	in_target_image = Input(shape=image_shape)
    
	merged = Concatenate()([in_src_image, in_target_image])
    
	d = Conv2D(64, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(merged)
	d = LeakyReLU(alpha=0.2)(d)
	d = Conv2D(128, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(d)
	d = BatchNormalization()(d)
	d = LeakyReLU(alpha=0.2)(d)
	d = Conv2D(256, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(d)
	d = BatchNormalization()(d)
	d = LeakyReLU(alpha=0.2)(d)
	d = Conv2D(512, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(d)
	d = BatchNormalization()(d)
	d = LeakyReLU(alpha=0.2)(d)
	d = Conv2D(512, (4,4), padding='same', kernel_initializer=init)(d)
	d = BatchNormalization()(d)
	d = LeakyReLU(alpha=0.2)(d)
	d = Conv2D(1, (4,4), padding='same', kernel_initializer=init)(d)
	patch_out = Activation('sigmoid')(d)
	model = Model([in_src_image, in_target_image], patch_out)
    
	opt = Adam(lr=0.0002, beta_1=0.5)
	model.compile(loss='binary_crossentropy', optimizer=opt, loss_weights=[0.5])
	return model

In [4]:
def define_encoder_block(layer_in, n_filters, batchnorm=True):
	init = RandomNormal(stddev=0.02)
	g = Conv2D(n_filters, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(layer_in)
	if batchnorm:
		g = BatchNormalization()(g, training=True)
	g = LeakyReLU(alpha=0.2)(g)
	return g

In [5]:
def decoder_block(layer_in, skip_in, n_filters, dropout=True):
	init = RandomNormal(stddev=0.02)
	g = Conv2DTranspose(n_filters, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(layer_in)
	g = BatchNormalization()(g, training=True)
	if dropout:
		g = Dropout(0.5)(g, training=True)
	g = Concatenate()([g, skip_in])
	g = Activation('relu')(g)
	return g

In [6]:
def define_generator(image_shape=(256,256,3)):
	init = RandomNormal(stddev=0.02)
	in_image = Input(shape=image_shape)
	e1 = define_encoder_block(in_image, 64, batchnorm=False)
	e2 = define_encoder_block(e1, 128)
	e3 = define_encoder_block(e2, 256)
	e4 = define_encoder_block(e3, 512)
	e5 = define_encoder_block(e4, 512)
	e6 = define_encoder_block(e5, 512)
	e7 = define_encoder_block(e6, 512)
	b = Conv2D(512, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(e7)
	b = Activation('relu')(b)
	d1 = decoder_block(b, e7, 512)
	d2 = decoder_block(d1, e6, 512)
	d3 = decoder_block(d2, e5, 512)
	d4 = decoder_block(d3, e4, 512, dropout=False)
	d5 = decoder_block(d4, e3, 256, dropout=False)
	d6 = decoder_block(d5, e2, 128, dropout=False)
	d7 = decoder_block(d6, e1, 64, dropout=False)
	g = Conv2DTranspose(image_shape[2], (4,4), strides=(2,2), padding='same', kernel_initializer=init)(d7)
	out_image = Activation('tanh')(g)
	model = Model(in_image, out_image)
	return model

In [7]:
def define_generator(image_shape=(256,256,3)):
	init = RandomNormal(stddev=0.02)
	in_image = Input(shape=image_shape)
	e1 = define_encoder_block(in_image, 64, batchnorm=False)
	e2 = define_encoder_block(e1, 128)
	e3 = define_encoder_block(e2, 256)
	e4 = define_encoder_block(e3, 512)
	e5 = define_encoder_block(e4, 512)
	e6 = define_encoder_block(e5, 512)
	e7 = define_encoder_block(e6, 512)
	b = Conv2D(512, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(e7)
	b = Activation('relu')(b)
	d1 = decoder_block(b, e7, 512)
	d2 = decoder_block(d1, e6, 512)
	d3 = decoder_block(d2, e5, 512)
	d4 = decoder_block(d3, e4, 512, dropout=False)
	d5 = decoder_block(d4, e3, 256, dropout=False)
	d6 = decoder_block(d5, e2, 128, dropout=False)
	d7 = decoder_block(d6, e1, 64, dropout=False)
	g = Conv2DTranspose(image_shape[2], (4,4), strides=(2,2), padding='same', kernel_initializer=init)(d7)
	out_image = Activation('tanh')(g)
	model = Model(in_image, out_image)
	return model

In [8]:
def define_gan(g_model, d_model, image_shape):
	for layer in d_model.layers:
		if not isinstance(layer, BatchNormalization):
			layer.trainable = False 
            
	in_src = Input(shape=image_shape)
	gen_out = g_model(in_src)
	dis_out = d_model([in_src, gen_out])
	model = Model(in_src, [dis_out, gen_out])
	opt = Adam(lr=0.0002, beta_1=0.5)
    
	model.compile(loss=['binary_crossentropy', 'mae'], 
               optimizer=opt, loss_weights=[1,100])
	return model

In [9]:
def generate_real_samples(dataset, n_samples, patch_shape):
	trainA, trainB = dataset
	ix = randint(0, trainA.shape[0], n_samples)
	X1, X2 = trainA[ix], trainB[ix]
	y = ones((n_samples, patch_shape, patch_shape, 1))
	return [X1, X2], y

In [10]:
def generate_fake_samples(g_model, samples, patch_shape):
	X = g_model.predict(samples)
	y = zeros((len(X), patch_shape, patch_shape, 1))
	return X, y

In [11]:
def summarize_performance(step, g_model, dataset, n_samples=3):
	[X_realA, X_realB], _ = generate_real_samples(dataset, n_samples, 1)
	X_fakeB, _ = generate_fake_samples(g_model, X_realA, 1)
	X_realA = (X_realA + 1) / 2.0
	X_realB = (X_realB + 1) / 2.0
	X_fakeB = (X_fakeB + 1) / 2.0

	for i in range(n_samples):
		plt.subplot(3, n_samples, 1 + i)
		plt.axis('off')
		plt.imshow(X_realA[i])

	for i in range(n_samples):
		plt.subplot(3, n_samples, 1 + n_samples + i)
		plt.axis('off')
		plt.imshow(X_fakeB[i])

	for i in range(n_samples):
		plt.subplot(3, n_samples, 1 + n_samples*2 + i)
		plt.axis('off')
		plt.imshow(X_realB[i])

	filename1 = 'plot_%06d.png' % (step+1)
	plt.savefig(os.path.join(r'.\sample_images', filename1))
	plt.close()

	filename2 = 'model_%06d.h5' % (step+1)
	g_model.save(os.path.join(r'.\models\gan', filename2))
	print('>Saved: %s and %s' % (filename1, filename2))

In [12]:
from tensorflow.keras.models import load_model, save_model

def save(gan, generator, discriminator):
    root_path = r'.\models\training'
    discriminator.trainable = False
    save_model(gan, os.path.join(root_path, 'gan'))
    discriminator.trainable = True
    save_model(generator, os.path.join(root_path, 'generator'))
    save_model(discriminator, os.path.join(root_path, 'discriminator'))

def load():
    root_path = ''
    discriminator = load_model(os.path.join(root_path, 'discriminator'))
    generator = load_model(os.path.join(root_path, 'generator'))
    gan = load_model(os.path.join(root_path, 'gan'))
    gan.summary()
    discriminator.summary()
    generator.summary()

    return gan, generator, discriminator

In [13]:
def train(d_model, g_model, gan_model, dataset, n_epochs=100, n_batch=1):
	n_patch = d_model.output_shape[1]
	trainA, trainB = dataset
	bat_per_epo = int(len(trainA) / n_batch)
	n_steps = bat_per_epo * n_epochs
	for i in range(n_steps):
		[X_realA, X_realB], y_real = generate_real_samples(dataset, n_batch, n_patch)
		X_fakeB, y_fake = generate_fake_samples(g_model, X_realA, n_patch)
		d_loss1 = d_model.train_on_batch([X_realA, X_realB], y_real)
		d_loss2 = d_model.train_on_batch([X_realA, X_fakeB], y_fake)
		g_loss, _, _ = gan_model.train_on_batch(X_realA, [y_real, X_realB])
		print(f'Эпоха: {((i+1) // bat_per_epo) + 1}')
		print('Итерация: %d, d1[%.3f] d2[%.3f] g[%.3f]' % (i+1, d_loss1, d_loss2, g_loss))
		if (i+1) % (bat_per_epo * 1) == 0: # Сохраняем модель генератора и набор изображений каждую (1) эпоху. 
			summarize_performance(i, g_model, dataset)
			save(gan_model, g_model, d_model)

In [14]:
from os import listdir
from numpy import asarray, load
from numpy import vstack
from tensorflow.keras.utils import img_to_array
from tensorflow.keras.utils import load_img
from numpy import savez_compressed
from matplotlib import pyplot
import numpy as np
import os

In [15]:
def load_images(images_path,  mask_path, size=(256,256)):
	src_list, tar_list = list(), list()
	images = sorted(os.listdir(images_path))
	masks = sorted(os.listdir(mask_path))
	for i in range(len(images)):      
		img_pixels = load_img(os.path.join(images_path, images[i]), target_size=size)
		img = img_to_array(img_pixels)

		mask_pixels = load_img(os.path.join(mask_path, masks[i]), target_size=size)
		mask = img_to_array(mask_pixels)
	
		src_list.append(img)
		tar_list.append(mask)

	return [asarray(src_list), asarray(tar_list)]

In [16]:
img_path = r'.\dataset\Forest Segmented\train_data\train_image\train'
mask_path = r'.\dataset\Forest Segmented\train_data\train_mask\train'
[src_images, tar_images] = load_images(img_path, mask_path)
print('Загружено: ', src_images.shape, tar_images.shape)

Загружено:  (3831, 256, 256, 3) (3831, 256, 256, 3)


In [17]:
data = [src_images, tar_images]

In [18]:
image_shape = src_images.shape[1:]

d_model = define_discriminator(image_shape)
g_model = define_generator(image_shape)
gan_model = define_gan(g_model, d_model, image_shape)

c:\ProgramData\Anaconda3\lib\site-packages\keras\initializers\initializers_v2.py:120: UserWarning: The initializer RandomNormal is unseeded and being called multiple times, which will return identical values  each time (even if the initializer is unseeded). Please update your code to provide a seed to the initializer, or avoid using the same initalizer instance more than once.
  warnings.warn(
c:\ProgramData\Anaconda3\lib\site-packages\keras\optimizers\optimizer_v2\adam.py:114: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super().__init__(name, **kwargs)


In [19]:
def preprocess_data(data): 
	img, mask = data[0], data[1]
	
	img = (img - 127.5) / 127.5
	mask = (mask - 127.5) / 127.5
	
	return [img, mask]

dataset = preprocess_data(data)

In [20]:
n_epochs = 200

In [21]:
import tensorflow as tf
tf.config.run_functions_eagerly(True) 

In [22]:
from datetime import datetime 

start1 = datetime.now() 

train(d_model, g_model, gan_model, dataset, n_epochs=n_epochs, n_batch=32) 

stop1 = datetime.now()

execution_time = stop1-start1
print("Время обучения модели: ", execution_time, f"(\nОдна эпоха: {(execution_time/n_epochs).total_seconds()/60} минут)")

c:\ProgramData\Anaconda3\lib\site-packages\tensorflow\python\data\ops\structured_function.py:264: UserWarning: Even though the `tf.config.experimental_run_functions_eagerly` option is set, this option does not apply to tf.data functions. To force eager execution of tf.data functions, please use `tf.data.experimental.enable_debug_mode()`.
  warnings.warn(


1/1 [==============================] - 12s 12s/step
Эпоха: 1
Итерация: 1, d1[0.421] d2[0.616] g[101.773]
1/1 [==============================] - 0s 46ms/step
Эпоха: 1
Итерация: 2, d1[0.895] d2[1.040] g[97.899]
1/1 [==============================] - 0s 46ms/step
Эпоха: 1
Итерация: 3, d1[1.015] d2[0.767] g[93.307]
1/1 [==============================] - 0s 46ms/step
Эпоха: 1
Итерация: 4, d1[0.486] d2[0.854] g[92.418]
1/1 [==============================] - 0s 47ms/step
Эпоха: 1
Итерация: 5, d1[0.542] d2[0.731] g[90.277]
1/1 [==============================] - 0s 44ms/step
Эпоха: 1
Итерация: 6, d1[0.362] d2[0.641] g[89.628]
1/1 [==============================] - 0s 47ms/step
Эпоха: 1
Итерация: 7, d1[0.313] d2[0.497] g[87.772]
1/1 [==============================] - 0s 49ms/step
Эпоха: 1
Итерация: 8, d1[0.292] d2[0.432] g[87.027]
1/1 [==============================] - 0s 45ms/step
Эпоха: 1
Итерация: 9, d1[0.293] d2[0.396] g[84.385]
1/1 [==============================] - 0s 46ms/step
Эпоха: 1
Ит

INFO:tensorflow:Assets written to: .\models\training\gan\assets


INFO:tensorflow:Assets written to: .\models\training\gan\assets


INFO:tensorflow:Assets written to: .\models\training\generator\assets


...

INFO:tensorflow:Assets written to: .\models\training\generator\assets


INFO:tensorflow:Assets written to: .\models\training\generator\assets


INFO:tensorflow:Assets written to: .\models\training\discriminator\assets


INFO:tensorflow:Assets written to: .\models\training\discriminator\assets


Время обучения модели:  10:39:02.663692 (
Одна эпоха: 3.1952219666666664 минут)


In [23]:
g_model.save(r'./models/Method2_Model.h5')